In [1]:
'''
Charles Diaz

Code Based on Philip Mocz' "Create Your Own Lattice Boltzmann Simulation (With Python)" tutorial,
- Article:https://medium.com/swlh/create-your-own-lattice-boltzmann-simulation-with-python-8759e8b53b1c
- Github:https://github.com/pmocz/latticeboltzmann-python/blob/main/latticeboltzmann.py
'''

%matplotlib osx

import matplotlib.pyplot as plt
import numpy as np
from matplotlib.animation import FFMpegWriter

metadata = dict(title='DensityIn2D', artist='',comment='')
writer = FFMpegWriter(fps=15, metadata=metadata)


def main():
    fig = plt.figure(figsize=(10,5))
    with writer.saving(fig, "animation.mp4", dpi=200):
        # Simulation parameters
        Nx                     = 600    # resolution x-dir
        Ny                     = 100    # resolution y-dir
        rho0                   = 100    # average density
        tau                    = 0.6    # collision timescale
        Nt                     = 4000   # number of timesteps
        plotRealTime = True # switch on for plotting as the simulation goes along

        # Lattice speeds / weights
        NL = 9
        idxs = np.arange(NL)
        cxs = np.array([0, 0, 1, 1, 1, 0,-1,-1,-1])
        cys = np.array([0, 1, 1, 0,-1,-1,-1, 0, 1])
        weights = np.array([4/9,1/9,1/36,1/9,1/36,1/9,1/36,1/9,1/36]) # sums to 1

        # Initial Conditions
        F = np.ones((Ny,Nx,NL)) * 0.1 #* rho0 / NL
        np.random.seed(42)
        F += 0.01*np.random.randn(Ny,Nx,NL)
        X, Y = np.meshgrid(range(Nx), range(Ny))
        for i in range(290,310):
            for j in range(Ny-51,Ny-49):
                F[j,i,3] += 3 * (1+0.2*np.cos(2*np.pi*X[j,i]/Nx*4))
        rho = np.sum(F,2)
        for i in idxs:
            F[:,:,i] *= rho0 / rho
        print(np.shape(X))

        # Floor and surface boundaries
        X, Y = np.meshgrid(range(Nx), range(Ny))

        floor = np.full((Ny, Nx), False)
        for i in range(0,Nx):
            for j in range(0,2):
                floor[j,i] = True

        surface = np.full((Ny, Nx), False)
        for i in range(0,Nx):
            for j in range(Ny-2,Ny):
                surface[j,i] = True

        right = np.full((Ny, Nx), False)
        for i in range(Nx-2,Nx):
            for j in range(0,Ny):
                right[j,i] = True

        left = np.full((Ny, Nx), False)
        for i in range(0,2):
            for j in range(0,Ny):
                right[j,i] = True

        walls = floor + left + right + surface

        print(walls)

        

        # Simulation Main Loop
        for it in range(Nt):

            # Drift
            for i, cx, cy in zip(idxs, cxs, cys):
                F[:,:,i] = np.roll(F[:,:,i], cx, axis=1)
                F[:,:,i] = np.roll(F[:,:,i], cy, axis=0)


            # Set reflective boundaries
            bndryF = F[walls,:]
            bndryF = bndryF[:,[0,5,6,7,8,1,2,3,4]]


            # Calculate fluid variables
            rho = np.sum(F,2)
            ux  = np.sum(F*cxs,2) / rho
            uy  = np.sum(F*cys,2) / rho


            # Apply Collision
            Feq = np.zeros(F.shape)
            for i, cx, cy, w in zip(idxs, cxs, cys, weights):
                Feq[:,:,i] = rho * w * ( 1 + 3*(cx*ux+cy*uy)  + 9*(cx*ux+cy*uy)**2/2 - 3*(ux**2+uy**2)/2 )

            F += -(1.0/tau) * (F - Feq)

            # Apply boundary 
            F[walls,:] = bndryF


            # plot in real time - color 1/2 particles blue, other half red
            if (plotRealTime and (it % 10) == 0) or (it == Nt-1):
                plt.cla()
                ux[walls] = 0
                uy[walls] = 0
                vorticity = (np.roll(ux, -1, axis=0) - np.roll(ux, 1, axis=0)) - (np.roll(uy, -1, axis=1) - np.roll(uy, 1, axis=1))
                vorticity[walls] = np.nan
                vorticity = np.ma.array(vorticity, mask=walls)
                #plt.imshow(vorticity, cmap='bwr')
                plt.imshow(np.sqrt(ux**2 + uy**2), cmap='plasma')
                #plt.imshow(rho, cmap='plasma')
                #plt.quiver(X, Y, ux, uy, scale=10)
                plt.imshow(~walls, cmap='gray', alpha=0.3)
                plt.clim(-.1, .1)
                ax = plt.gca()
                ax.invert_yaxis()
                ax.get_xaxis().set_visible(False)
                ax.get_yaxis().set_visible(False)
                writer.grab_frame()
                ax.set_aspect('equal')
                plt.pause(0.001)
    return 0



if __name__== "__main__":
  main()


(100, 600)
[[ True  True  True ...  True  True  True]
 [ True  True  True ...  True  True  True]
 [ True  True False ... False  True  True]
 ...
 [ True  True False ... False  True  True]
 [ True  True  True ...  True  True  True]
 [ True  True  True ...  True  True  True]]
